<a href="https://colab.research.google.com/github/daddyofadoggy/AI_Agents_HF/blob/main/agent_rag.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Agentic RAG: turbocharge your RAG with query reformulation and self-query! 🚀
_Authored by: [Aymeric Roucher](https://huggingface.co/m-ric)_

> This tutorial is advanced. You should have notions from [this other cookbook](advanced_rag) first!

> Reminder: Retrieval-Augmented-Generation (RAG) is “using an LLM to answer a user query, but basing the answer on information retrieved from a knowledge base”. It has many advantages over using a vanilla or fine-tuned LLM: to name a few, it allows to ground the answer on true facts and reduce confabulations, it allows to provide the LLM with domain-specific knowledge, and it allows fine-grained control of access to information from the knowledge base.

But vanilla RAG has limitations, most importantly these two:
- It **performs only one retrieval step**: if the results are bad, the generation in turn will be bad.
- __Semantic similarity is computed with the *user query* as a reference__, which might be suboptimal: for instance, the user query will often be a question and the document containing the true answer will be in affirmative voice, so its similarity score will be downgraded compared to other source documents in the interrogative form, leading to a risk of missing the relevant information.

But we can alleviate these problems by making a **RAG agent: very simply, an agent armed with a retriever tool!**

This agent will: ✅ Formulate the query itself and ✅ Critique to re-retrieve if needed.

So it should naively recover some advanced RAG techniques!
- Instead of directly using the user query as the reference in semantic search, the agent formulates itself a reference sentence that can be closer to the targeted documents, as in [HyDE](https://huggingface.co/papers/2212.10496)
- The agent can the generated snippets and re-retrieve if needed, as in [Self-Query](https://docs.llamaindex.ai/en/stable/examples/evaluation/RetryQuery/)

Let's build this system. 🛠️

Run the line below to install required dependencies:

In [ ]:
from google.colab import userdata
userdata.get('HF_TOKEN')

In [ ]:
!pip install pandas langchain langchain-community sentence-transformers faiss-cpu smolagents --upgrade -q

Let's login in order to call the HF Inference API:

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
!rm -rf ~/.cache/huggingface/datasets/nielsr___huggingface-hub-docs*

We first load a knowledge base on which we want to perform RAG: this dataset is a compilation of the documentation pages for many `huggingface` packages, stored as markdown.

In [ ]:
#import pandas as pd

#url = "https://huggingface.co/datasets/nielsr/huggingface-hub-docs/resolve/main/data/train-00000-of-00001.parquet"

#df = pd.read_parquet(url)

#print(df.head())


In [ ]:
#df.shape

In [101]:
import pandas as pd


# Load into pandas DataFrame locally
df = pd.read_csv('/content/huggingface_doc.csv')

# Preview
print(df.shape)
print(df.head())

(2647, 2)
                                                text  \
0   Create an Endpoint\n\nAfter your first login,...   
1   Choosing a metric for your task\n\n**So you'v...   
2   主要特点\n\n让我们来介绍一下 Gradio 最受欢迎的一些功能！这里是 Gradio ...   
3  !--Copyright 2023 The HuggingFace Team. All ri...   
4   Gradio Demo: blocks_random_slider\n\n\n```\n!...   

                                              source  
0  huggingface/hf-endpoints-documentation/blob/ma...  
1  huggingface/evaluate/blob/main/docs/source/cho...  
2  gradio-app/gradio/blob/main/guides/cn/01_getti...  
3  huggingface/transformers/blob/main/docs/source...  
4  gradio-app/gradio/blob/main/demo/blocks_random...  


In [ ]:
df

In [ ]:
#from datasets import get_dataset_split_names, load_dataset_builder

#print(get_dataset_split_names("nielsr/huggingface-hub-docs"))
#builder = load_dataset_builder("nielsr/huggingface-hub-docs")
#print(builder.info.features)


In [102]:
import datasets
from datasets import Dataset

knowledge_base = Dataset.from_pandas(df)


In [103]:
knowledge_base

Dataset({
    features: ['text', 'source'],
    num_rows: 2647
})

In [104]:
knowledge_base[0]

{'text': ' Create an Endpoint\n\nAfter your first login, you will be directed to the [Endpoint creation page](https://ui.endpoints.huggingface.co/new). As an example, this guide will go through the steps to deploy [distilbert-base-uncased-finetuned-sst-2-english](https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english) for text classification. \n\n## 1. Enter the Hugging Face Repository ID and your desired endpoint name:\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_repository.png" alt="select repository" />\n\n## 2. Select your Cloud Provider and region. Initially, only AWS will be available as a Cloud Provider with the `us-east-1` and `eu-west-1` regions. We will add Azure soon, and if you need to test Endpoints with other Cloud Providers or regions, please let us know.\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_region.png" alt="select region" />\n\n## 3. Defi

Now we prepare the knowledge base by processing the dataset and storing it into a vector database to be used by the retriever.

We use [LangChain](https://python.langchain.com/) for its excellent vector database utilities.
For the embedding model, we use [thenlper/gte-small](https://huggingface.co/thenlper/gte-small) since it performed well in our `RAG_evaluation` cookbook.

In [105]:
from tqdm import tqdm
from transformers import AutoTokenizer
from langchain.docstore.document import Document
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.vectorstores.utils import DistanceStrategy

source_docs = [
    Document(page_content=doc["text"], metadata={"source": doc["source"].split("/")[1]})
    for doc in knowledge_base
]

text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(
    AutoTokenizer.from_pretrained("thenlper/gte-small"),
    chunk_size=200,
    chunk_overlap=20,
    add_start_index=True,
    strip_whitespace=True,
    separators=["\n\n", "\n", ".", " ", ""],
)

# Split docs and keep only unique ones
print("Splitting documents...")
docs_processed = []
unique_texts = {}
for doc in tqdm(source_docs):
    new_docs = text_splitter.split_documents([doc])
    for new_doc in new_docs:
        if new_doc.page_content not in unique_texts:
            unique_texts[new_doc.page_content] = True
            docs_processed.append(new_doc)

print(
    "Embedding documents... This should take a few minutes (5 minutes on MacBook with M1 Pro)"
)
embedding_model = HuggingFaceEmbeddings(model_name="thenlper/gte-small")
vectordb = FAISS.from_documents(
    documents=docs_processed,
    embedding=embedding_model,
    distance_strategy=DistanceStrategy.COSINE,
)

Splitting documents...


100%|██████████| 2647/2647 [03:10<00:00, 13.92it/s]


Embedding documents... This should take a few minutes (5 minutes on MacBook with M1 Pro)


KeyboardInterrupt: 

In [106]:
len(source_docs)

2647

In [107]:
source_docs[1]

Document(metadata={'source': 'evaluate'}, page_content=' Choosing a metric for your task\n\n**So you\'ve trained your model and want to see how well it’s doing on a dataset of your choice. Where do you start?**\n\nThere is no “one size fits all” approach to choosing an evaluation metric, but some good guidelines to keep in mind are:\n\n## Categories of metrics\n\nThere are 3 high-level categories of metrics:\n\n1. *Generic metrics*, which can be applied to a variety of situations and datasets, such as precision and accuracy.\n2. *Task-specific metrics*, which are limited to a given task, such as Machine Translation (often evaluated using metrics [BLEU](https://huggingface.co/metrics/bleu) or [ROUGE](https://huggingface.co/metrics/rouge)) or Named Entity Recognition (often evaluated with [seqeval](https://huggingface.co/metrics/seqeval)).\n3. *Dataset-specific metrics*, which aim to measure model performance on specific benchmarks: for instance, the [GLUE benchmark](https://huggingface.

In [108]:
len(docs_processed)

39785

In [109]:
docs_processed[0]

Document(metadata={'source': 'hf-endpoints-documentation', 'start_index': 1}, page_content='Create an Endpoint\n\nAfter your first login, you will be directed to the [Endpoint creation page](https://ui.endpoints.huggingface.co/new). As an example, this guide will go through the steps to deploy [distilbert-base-uncased-finetuned-sst-2-english](https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english) for text classification. \n\n## 1. Enter the Hugging Face Repository ID and your desired endpoint name:\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_repository.png" alt="select repository" />')

In [110]:
docs_processed[0].metadata

{'source': 'hf-endpoints-documentation', 'start_index': 1}

In [111]:
docs_processed[1].page_content

'## 2. Select your Cloud Provider and region. Initially, only AWS will be available as a Cloud Provider with the `us-east-1` and `eu-west-1` regions. We will add Azure soon, and if you need to test Endpoints with other Cloud Providers or regions, please let us know.\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_region.png" alt="select region" />\n\n## 3. Define the [Security Level](security) for the Endpoint:\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_security.png" alt="define security" />'

In [112]:
docs_processed[1]

Document(metadata={'source': 'hf-endpoints-documentation', 'start_index': 568}, page_content='## 2. Select your Cloud Provider and region. Initially, only AWS will be available as a Cloud Provider with the `us-east-1` and `eu-west-1` regions. We will add Azure soon, and if you need to test Endpoints with other Cloud Providers or regions, please let us know.\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_region.png" alt="select region" />\n\n## 3. Define the [Security Level](security) for the Endpoint:\n\n<img src="https://raw.githubusercontent.com/huggingface/hf-endpoints-documentation/main/assets/1_security.png" alt="define security" />')

In [113]:
vectordb

In [114]:
import numpy as np

# Access internal document store
docstore = vectordb.docstore._dict  # {uuid: Document}

# Access FAISS index (vectors)
index = vectordb.index

# Loop through top 5 documents
for i, (doc_id, doc) in enumerate(docstore.items()):
    if i >= 5:
        break

    print(f"\n🔹 Document {i+1} — ID: {doc_id}")
    print("📄 Content:", doc.page_content[:300], "..." if len(doc.page_content) > 300 else "")

    # Get embedding vector by position
    embedding_vector = index.reconstruct(i)
    print(len(embedding_vector))
    print("📊 Embedding vector (first 10 dims):", np.round(embedding_vector[:10], 4), "...")



🔹 Document 1 — ID: 550585a2-5f4e-497a-9afd-2fcf68715ff2
📄 Content: guides/manage_spaces: guides/manage-spaces
guides/webhooks_server: guides/webhooks
hf_transfer: package_reference/environment_variables#hfhubenablehftransfer
how-to-cache: guides/manage-cache
how-to-discussions-and-pull-requests: guides/community
how-to-downstream: guides/download
how-to-inference:  ...
384
📊 Embedding vector (first 10 dims): [-0.0347 -0.0088  0.0568 -0.0054  0.0044 -0.0013 -0.0093  0.0481 -0.0006
 -0.0042] ...

🔹 Document 2 — ID: ada77aef-f73f-4b81-8510-99388386c75d
📄 Content: <!--⚠️ Note that this file is in Markdown but contains specific syntax for our doc-builder (similar to MDX) that may not be
rendered properly in your Markdown viewer.
-->

# Quickstart

The [Hugging Face Hub](https://huggingface.co/) is the go-to place for sharing machine learning
models, demos, dat ...
384
📊 Embedding vector (first 10 dims): [-0.0558 -0.0286  0.0286  0.0028  0.0422  0.0024 -0.0032 -0.0177  0.0012
 -0.0183] ...


In [115]:
len(docstore.items())

969

Now the database is ready: let’s build our agentic RAG system!

👉 We only need a `RetrieverTool` that our agent can leverage to retrieve information from the knowledge base.

Since we need to add a vectordb as an attribute of the tool, we cannot simply use the [simple tool constructor](https://huggingface.co/docs/transformers/main/en/agents#create-a-new-tool) with a `@tool` decorator: so we will follow the advanced setup highlighted in the [advanced agents documentation](https://huggingface.co/docs/transformers/main/en/agents_advanced#directly-define-a-tool-by-subclassing-tool-and-share-it-to-the-hub).

In [116]:
from smolagents import Tool
from langchain_core.vectorstores import VectorStore


class RetrieverTool(Tool):
    name = "retriever"
    description = "Using semantic similarity, retrieves some documents from the knowledge base that have the closest embeddings to the input query."
    inputs = {
        "query": {
            "type": "string",
            "description": "The query to perform. This should be semantically close to your target documents. Use the affirmative form rather than a question.",
        }
    }
    output_type = "string"

    def __init__(self, vectordb: VectorStore, **kwargs):
        super().__init__(**kwargs)
        self.vectordb = vectordb

    def forward(self, query: str) -> str:
        assert isinstance(query, str), "Your search query must be a string"

        docs = self.vectordb.similarity_search(
            query,
            k=7,
        )

        return "\nRetrieved documents:\n" + "".join(
            [
                f"===== Document {str(i)} =====\n" + doc.page_content
                for i, doc in enumerate(docs)
            ]
        )

Now it’s straightforward to create an agent that leverages this tool!

The agent will need these arguments upon initialization:
- *`tools`*: a list of tools that the agent will be able to call.
- *`model`*: the LLM that powers the agent.

Our `model` must be a callable that takes as input a list of [messages](https://huggingface.co/docs/transformers/main/chat_templating) and returns text. It also needs to accept a `stop_sequences` argument that indicates when to stop its generation. For convenience, we directly use the `InferenceClientModel` class provided in the package to get a LLM engine that calls our [Inference API](https://huggingface.co/docs/api-inference/en/index).

And we use [meta-llama/Llama-3.1-70B-Instruct](https://huggingface.co/meta-llama/Llama-3.1-70B-Instruct), served for free on Hugging Face's Inference API!

_Note:_ The Inference API hosts models based on various criteria, and deployed models may be updated or replaced without prior notice. Learn more about it [here](https://huggingface.co/docs/api-inference/supported-models).

In [117]:
from smolagents import InferenceClientModel, ToolCallingAgent

model = InferenceClientModel("meta-llama/Llama-3.1-70B-Instruct")

retriever_tool = RetrieverTool(vectordb)
agent = ToolCallingAgent(
    tools=[retriever_tool], model=model
)

Since we initialized the agent as a `ReactJsonAgent`, it has been automatically given a default system prompt that tells the LLM engine to process step-by-step and generate tool calls as JSON blobs (you could replace this prompt template with your own as needed).

Then when its `.run()` method is launched, the agent takes care of calling the LLM engine, parsing the tool call JSON blobs and executing these tool calls, all in a loop that ends only when the final answer is provided.

In [118]:
agent_output = agent.run("How can I push a model to the Hub?")

print("Final output:")
print(agent_output)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ How can I push a model to the Hub?                                                                              │
│                                                                                                                 │
╰─ InferenceClientModel - meta-llama/Llama-3.1-70B-Instruct ──────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'retriever' with arguments: {'query': 'How can I push a model to the Hub?'}                       │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Observations: Retrieved documents:
===== Document 0 =====
```python
def push_to_hub(model: MyModelClass, repo_name: str) -> None:
   api = HfApi()

   # Create repo if not existing yet and get the associated repo_id
   repo_id = api.create_repo(repo_name, exist_ok=True)

   # Save all files in a temporary directory and push them in a single commit
   with TemporaryDirectory() as tmpdir:
      tmpdir = Path(tmpdir)

      # Save weights
      save_model(model, tmpdir / "model.safetensors")

      # Generate model card
      card = generate_model_card(model)
      (tmpdir / "README.md").write_text(card)

      # Save logs
      # Save figures
      # Save evaluation metrics
      # ...===== Document 1 =====
<!-- Generated using https://www.tablesgenerator.com/markdown_tables -->
| Integration | Using helpers | Using |`ModelHubMixin`] |
|:---:|:---:|:---:|
| User experience | `model = load_from_hub(...)`<br>`push_to_hub(model, ...)` | `model = 
MyModel.from_pretrained(...)`<br>`model.push_to_hub(...)` |
| Flexibility | Very flexible.<br>You fully control the implementation. | Less flexible.<br>Your framework must 
have a model class. |===== Document 2 =====
## Share Model Cards

If you're authenticated with the Hugging Face Hub (either by using `huggingface-cli login` or |`login`]), you can 
push cards to the Hub by simply calling |`ModelCard.push_to_hub`]. Let's take a look at how to do that...

First, we'll create a new repo called 'hf-hub-modelcards-pr-test' under the authenticated user's namespace:

```python
from huggingface_hub import whoami, create_repo

user = whoami()|'name']
repo_id = f'{user}/hf-hub-modelcards-pr-test'
url = create_repo(repo_id, exist_ok=True)
```===== Document 3 =====
There are four main ways to integrate a library with the Hub:
1. **Push to Hub:** implement a method to upload a model to the Hub. This includes the model weights, as well as
   |the model card](https://huggingface.co/docs/huggingface_hub/how-to-model-cards) and any other relevant 
information
   or data necessary to run the model (for example, training logs). This method is often called `push_to_hub()`.
2. **Download from Hub:** implement a method to load a model from the Hub. The method should download the model
   configuration/weights and load the model. This method is often called `from_pretrained` or `load_from_hub()`.
3. **Inference API:** use our servers to run inference on models supported by your library for free.===== Document 
4 =====
>>> model = MyCustomModel(size=256, device="gpu")

# Save model weights to local directory
>>> model.save_pretrained("my-awesome-model")

# Push model weights to the Hub
>>> model.push_to_hub("my-awesome-model")

# Download and initialize weights from the Hub
>>> reloaded_model = MyCustomModel.from_pretrained("username/my-awesome-model")
>>> reloaded_model.size
256===== Document 5 =====
</Tip>

## Load a Model Card from the Hub

To load an existing card from the Hub, you can use the |`ModelCard.load`] function. Here, we'll load the card from 
|`nateraw/vit-base-beans`](https://huggingface.co/nateraw/vit-base-beans).

```python
from huggingface_hub import ModelCard

card = ModelCard.load('nateraw/vit-base-beans')
```===== Document 6 =====
The |`ModelHubMixin`] class implements 3 *public* methods (`push_to_hub`, `save_pretrained` and `from_pretrained`).
Those
are the methods that your users will call to load/save models with your library. |`ModelHubMixin`] also defines 2
*private* methods (`_save_pretrained` and `_from_pretrained`). Those are the ones you must implement. So to 
integrate
your library, you should:

[Step 1: Duration 0.97 seconds| Input tokens: 1,198 | Output tokens: 28]

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 2 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'final_answer' with arguments: {'answer': 'To push a model to the Hub, you can use the            │
│ `push_to_hub` method from the `ModelHubMixin` class. This method takes the model and the repository name as     │
│ arguments. You can also use the `create_repo` function from the `huggingface_hub` library to create a new       │
│ repository if it does not exist yet.'}                                                                          │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Final answer: To push a model to the Hub, you can use the `push_to_hub` method from the `ModelHubMixin` class. This
method takes the model and the repository name as arguments. You can also use the `create_repo` function from the 
`huggingface_hub` library to create a new repository if it does not exist yet.

[Step 2: Duration 1.49 seconds| Input tokens: 3,383 | Output tokens: 115]

Final output:
To push a model to the Hub, you can use the `push_to_hub` method from the `ModelHubMixin` class. This method takes the model and the repository name as arguments. You can also use the `create_repo` function from the `huggingface_hub` library to create a new repository if it does not exist yet.


## Agentic RAG vs. standard RAG

Does the agent setup make a better RAG system? Well, let's compare it to a standard RAG system using LLM Judge!

We will use [meta-llama/Meta-Llama-3-70B-Instruct](https://huggingface.co/meta-llama/Meta-Llama-3-70B-Instruct) for evaluation since it's one of the strongest OS models we tested for LLM judge use cases.

In [119]:
url = "https://huggingface.co/datasets/m-ric/huggingface_doc_qa_eval/resolve/main/data/train-00000-of-00001.parquet"

# Load into pandas DataFrame
df2 = pd.read_parquet(url)
df2.head()

context  \
0   `tokenizers-linux-x64-musl`\n\nThis is the **...   
1  !--Copyright 2023 The HuggingFace Team. All ri...   
2   Paper Pages\n\nPaper pages allow people to fi...   
3   Datasets server API\n\n> API on 🤗 datasets\n\...   
4  !--Copyright 2022 The HuggingFace Team. All ri...   

                                            question  \
0  What architecture is the `tokenizers-linux-x64...   
1  What is the purpose of the BLIP-Diffusion mode...   
2  How can a user claim authorship of a paper on ...   
3  What is the purpose of the /healthcheck endpoi...   
4  What is the default context window size for Lo...   

                                              answer  \
0                          x86_64-unknown-linux-musl   
1  The BLIP-Diffusion model is designed for contr...   
2  By clicking their name on the corresponding Pa...   
3                          Ensure the app is running   
4                                         127 tokens   

                                          source_doc  standalone_score  \
0  huggingface/tokenizers/blob/main/bindings/node...                 5   
1  huggingface/diffusers/blob/main/docs/source/en...                 5   
2  huggingface/hub-docs/blob/main/docs/hub/paper-...                 5   
3  huggingface/datasets-server/blob/main/services...                 5   
4  huggingface/transformers/blob/main/docs/source...                 5   

                                     standalone_eval  relatedness_score  \
0  The question is asking about the specific arch...                  5   
1  The question is asking for the purpose of a sp...                  5   
2  The question is clear and does not depend on a...                  5   
3  The question is asking for the purpose of a sp...                  5   
4  The question is asking for a specific paramete...                  5   

                                    relatedness_eval  relevance_score  \
0  The context directly specifies the architectur...                3   
1  The context provides a detailed description of...                3   
2  The context provides a clear explanation of ho...                3   
3  The context directly states the purpose of the...                4   
4  The context provides a specific detail about t...                3   

                                      relevance_eval  
0  The question is asking for specific technical ...  
1  The question asks about the purpose of the BLI...  
2  The question is specific to the Hugging Face H...  
3  The question is specific and technical, asking...  
4  This question is specific and technical, askin...

In [120]:
from datasets import Dataset

# Convert to Hugging Face Dataset
eval_dataset = Dataset.from_pandas(df2)

In [121]:
eval_dataset[0]

{'context': ' `tokenizers-linux-x64-musl`\n\nThis is the **x86_64-unknown-linux-musl** binary for `tokenizers`\n',
 'question': 'What architecture is the `tokenizers-linux-x64-musl` binary designed for?\n',
 'answer': 'x86_64-unknown-linux-musl',
 'source_doc': 'huggingface/tokenizers/blob/main/bindings/node/npm/linux-x64-musl/README.md',
 'standalone_score': 5,
 'standalone_eval': 'The question is asking about the specific architecture for which a binary file, named `tokenizers-linux-x64-musl`, is designed. The terms used in the question are technical but do not depend on a specific context to be understood. The question is clear and can be understood by someone familiar with computer architecture and software without additional context.\n\n',
 'relatedness_score': 5,
 'relatedness_eval': 'The context directly specifies the architecture for which the `tokenizers-linux-x64-musl` binary is designed. It states that this is the binary for `tokenizers` intended for the **x86_64-unknown-lin

In [122]:
eval_dataset

Dataset({
    features: ['context', 'question', 'answer', 'source_doc', 'standalone_score', 'standalone_eval', 'relatedness_score', 'relatedness_eval', 'relevance_score', 'relevance_eval'],
    num_rows: 65
})

Before running the test let's make the agent less verbose.

In [ ]:
#import logging

#agent.logger.setLevel(logging.WARNING) # Let's reduce the agent's verbosity level

#eval_dataset = datasets.load_dataset("m-ric/huggingface_doc_qa_eval", split="train")

In [124]:
outputs_agentic_rag = []

for example in tqdm(eval_dataset):
    question = example["question"]

    enhanced_question = f"""Using the information contained in your knowledge base, which you can access with the 'retriever' tool,
give a comprehensive answer to the question below.
Respond only to the question asked, response should be concise and relevant to the question.
If you cannot find information, do not give up and try calling your retriever again with different arguments!
Make sure to have covered the question completely by calling the retriever tool several times with semantically different queries.
Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".

Question:
{question}"""
    answer = agent.run(enhanced_question)
    print("=======================================================")
    print(f"Question: {question}")
    print(f"Answer: {answer}")
    print(f'True answer: {example["answer"]}')

    results_agentic = {
        "question": question,
        "true_answer": example["answer"],
        "source_doc": example["source_doc"],
        "generated_answer": answer,
    }
    outputs_agentic_rag.append(results_agentic)

  0%|          | 0/65 [00:00<?, ?it/s]

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Using the information contained in your knowledge base, which you can access with the 'retriever' tool,         │
│ give a comprehensive answer to the question below.                                                              │
│ Respond only to the question asked, response should be concise and relevant to the question.                    │
│ If you cannot find information, do not give up and try calling your retriever again with different arguments!   │
│ Make sure to have covered the question completely by calling the retriever tool several times with semantically │
│ different queries.                                                                                              │
│ Your queries should not be questions but affirmative form sentences: e.g. rather than "How do I load a model    │
│ from the Hub in bf16?", query should be "load a model from the Hub bf16 weights".                               │
│                                                                                                                 │
│ Question:                                                                                                       │
│ What architecture is the `tokenizers-linux-x64-musl` binary designed for?                                       │
│                                                                                                                 │
╰─ InferenceClientModel - meta-llama/Llama-3.1-70B-Instruct ──────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'retriever' with arguments: {'query': 'The architecture of the `tokenizers-linux-x64-musl` binary │
│ is'}                                                                                                            │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Observations: Retrieved documents:
===== Document 0 =====
```===== Document 1 =====
```python===== Document 2 =====
</Tip>

### Manage multiple tokens locally

You can save multiple tokens on your machine by simply logging in with the |`login`] command with each token. If 
you need to switch between these tokens locally, you can use the |`auth switch`] command:

```bash
huggingface-cli auth switch
```

This command will prompt you to select a token by its name from a list of saved tokens. Once selected, the chosen 
token becomes the _active_ token, and it will be used for all interactions with the Hub.


You can list all available access tokens on your machine with `huggingface-cli auth list`.

### Environment variable===== Document 3 =====
### Specify a commit message

Use the `--commit-message` and `--commit-description` to set a custom message and description for your commit 
instead of the default one

```bash
>>> huggingface-cli upload Wauplin/my-cool-model ./models . --commit-message="Epoch 34/50" 
--commit-description="Val accuracy: 68%. Check tensorboard for more details."
...
https://huggingface.co/Wauplin/my-cool-model/tree/main
```

### Specify a token

To upload files, you must use a token. By default, the token saved locally (using `huggingface-cli login`) will be 
used. If you want to authenticate explicitly, use the `--token` option:===== Document 4 =====
### Specify a token

To access private or gated repositories, you must use a token. By default, the token saved locally (using 
`huggingface-cli login`) will be used. If you want to authenticate explicitly, use the `--token` option:

```bash
>>> huggingface-cli download gpt2 config.json --token=hf_****
/home/wauplin/.cache/huggingface/hub/models--gpt2/snapshots/11c5a3d5811f50298f278a704980280950aedb10/config.json
```

### Quiet mode===== Document 5 =====
```text
Model Name: gpt2
Tags: |'pytorch', 'tf', 'jax', 'tflite', 'rust', 'safetensors', 'gpt2', 'text-generation', 'en', 
'doi:10.57967/hf/0039', 'transformers', 'exbert', 'license:mit', 'has_space']
Task: text-generation
```

## Windows limitations===== Document 6 =====
```bash
# Or using an environment variable
>>> huggingface-cli login --token $HF_TOKEN --add-to-git-credential
Token is valid (permission: write).
The token `token_name` has been saved to /home/wauplin/.cache/huggingface/stored_tokens
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /home/wauplin/.cache/huggingface/token
Login successful
The current active token is: `token_name`
```

For more details about authentication, check out |this section](../quick-start#authentication).

## huggingface-cli whoami

...

╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ Calling tool: 'final_answer' with arguments: {'answer': 'pip install optimum[openvino]'}                        │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

Final answer: pip install optimum[openvino]

[Step 3: Duration 0.80 seconds| Input tokens: 6,760 | Output tokens: 79]

100%|██████████| 65/65 [02:43<00:00,  2.51s/it]

Question: What is the command to install the latest version of Optimum with OpenVINO support?

Answer: pip install optimum[openvino]
True answer: pip install --upgrade-strategy eager optimum["openvino"]


In [125]:
from huggingface_hub import InferenceClient

reader_llm = InferenceClient("Qwen/Qwen2.5-72B-Instruct")

outputs_standard_rag = []

for example in tqdm(eval_dataset):
    question = example["question"]
    context = retriever_tool(question)

    prompt = f"""Given the question and supporting documents below, give a comprehensive answer to the question.
Respond only to the question asked, response should be concise and relevant to the question.
Provide the number of the source document when relevant.
If you cannot find information, do not give up and try calling your retriever again with different arguments!

Question:
{question}

{context}
"""
    messages = [{"role": "user", "content": prompt}]
    answer = reader_llm.chat_completion(messages).choices[0].message.content

    print("=======================================================")
    print(f"Question: {question}")
    print(f"Answer: {answer}")
    print(f'True answer: {example["answer"]}')

    results_agentic = {
        "question": question,
        "true_answer": example["answer"],
        "source_doc": example["source_doc"],
        "generated_answer": answer,
    }
    outputs_standard_rag.append(results_agentic)

  2%|▏         | 1/65 [00:01<01:15,  1.19s/it]

Question: What architecture is the `tokenizers-linux-x64-musl` binary designed for?

Answer: The `tokenizers-linux-x64-musl` binary is designed for the x86_64 architecture, and it is built for systems using the musl libc library. This indicates it is intended for Linux systems that use musl as their C standard library, often found in lightweight or embedded systems.
True answer: x86_64-unknown-linux-musl


  3%|▎         | 2/65 [00:02<01:36,  1.53s/it]

Question: What is the purpose of the BLIP-Diffusion model?

Answer: The provided documents do not contain specific information about the BLIP-Diffusion model. However, based on the context, BLIP-Diffusion likely combines elements of the BLIP (Berkeley Large-scale Image Pre-training) and Diffusion models. The purpose of the BLIP-Diffusion model is to integrate the strengths of both models to improve tasks such as image captioning, text-to-image generation, and other multimodal tasks that require understanding and generating images based on textual input. If you need more detailed information, please provide additional sources or context.
True answer: The BLIP-Diffusion model is designed for controllable text-to-image generation and editing.


  5%|▍         | 3/65 [00:09<04:10,  4.04s/it]

...

Question: What is the name of the open-source library created by Hugging Face to simplify Transformer acceleration?

Answer: The open-source library created by Hugging Face to simplify Transformer acceleration is not directly mentioned in the provided documents. However, the context suggests that the `huggingface_hub` library (mentioned in all documents) is primarily for interacting with the Hugging Face Hub, which hosts and shares machine learning models, including Transformers. For specific Transformer acceleration, you might be referring to the `transformers` library, which is a more direct tool for working with and optimizing Transformer models. However, since this is not explicitly stated in the documents, I cannot confirm with certainty. If you are looking for a library specifically for acceleration, you may need to check the `transformers` documentation or other Hugging Face resources.
True answer: Optimum


 98%|█████████▊| 64/65 [01:57<00:02,  2.03s/it]

Question: What parameter is used to ensure that elements in a row have the same height in Gradio?

Answer: The provided documents do not contain information about a parameter to ensure that elements in a row have the same height in Gradio. To achieve this, you may need to use the `equal_height` parameter in the `gr.Row` component. This parameter ensures that all elements within the row have the same height. For example:

```python
with gr.Blocks() as demo:
    with gr.Row(equal_height=True):
        # Add your components here
```

However, this information is not found in the provided sources.
True answer: equal_height


100%|██████████| 65/65 [01:58<00:00,  1.83s/it]

Question: What is the command to install the latest version of Optimum with OpenVINO support?

Answer: The command to install the latest version of Optimum with OpenVINO support is not directly provided in the given documents. However, you can typically install it using pip with the following command:

```bash
pip install 'optimum[openvino]'
```

This command installs the Optimum library along with the OpenVINO dependencies. If this specific command does not work, you may need to refer to the Optimum or OpenVINO documentation for the most up-to-date installation instructions.
True answer: pip install --upgrade-strategy eager optimum["openvino"]


The evaluation prompt follows some of the best principles shown in [our llm_judge cookbook](llm_judge): it follows a small integer Likert scale, has clear criteria, and a description for each score.

In [128]:
outputs_agentic_rag[0]

{'question': 'What architecture is the `tokenizers-linux-x64-musl` binary designed for?\n',
 'true_answer': 'x86_64-unknown-linux-musl',
 'source_doc': 'huggingface/tokenizers/blob/main/bindings/node/npm/linux-x64-musl/README.md',
 'generated_answer': 'The `tokenizers-linux-x64-musl` binary is designed for Linux x64 architecture.'}

In [129]:
outputs_standard_rag[0]

{'question': 'What architecture is the `tokenizers-linux-x64-musl` binary designed for?\n',
 'true_answer': 'x86_64-unknown-linux-musl',
 'source_doc': 'huggingface/tokenizers/blob/main/bindings/node/npm/linux-x64-musl/README.md',
 'generated_answer': 'The `tokenizers-linux-x64-musl` binary is designed for the x86_64 architecture, and it is built for systems using the musl libc library. This indicates it is intended for Linux systems that use musl as their C standard library, often found in lightweight or embedded systems.'}

In [130]:
EVALUATION_PROMPT = """You are a fair evaluator language model.

You will be given an instruction, a response to evaluate, a reference answer that gets a score of 3, and a score rubric representing a evaluation criteria are given.
1. Write a detailed feedback that assess the quality of the response strictly based on the given score rubric, not evaluating in general.
2. After writing a feedback, write a score that is an integer between 1 and 3. You should refer to the score rubric.
3. The output format should look as follows: \"Feedback: {{write a feedback for criteria}} [RESULT] {{an integer number between 1 and 3}}\"
4. Please do not generate any other opening, closing, and explanations. Be sure to include [RESULT] in your output.
5. Do not score conciseness: a correct answer that covers the question should receive max score, even if it contains additional useless information.

The instruction to evaluate:
{instruction}

Response to evaluate:
{response}

Reference Answer (Score 3):
{reference_answer}

Score Rubrics:
[Is the response complete, accurate, and factual based on the reference answer?]
Score 1: The response is completely incomplete, inaccurate, and/or not factual.
Score 2: The response is somewhat complete, accurate, and/or factual.
Score 3: The response is completely complete, accurate, and/or factual. Also

Feedback:"""

In [131]:
from huggingface_hub import InferenceClient

evaluation_client = InferenceClient("meta-llama/Llama-3.1-70B-Instruct")

In [147]:
from huggingface_hub import InferenceClient
from transformers import pipeline

evaluation_client = pipeline('text-generation', model = "gpt2")
import pandas as pd

results = {}
for system_type, outputs in [
    ("agentic", outputs_agentic_rag),
    ("standard", outputs_standard_rag),
]:
    for experiment in tqdm(outputs):
        eval_prompt = EVALUATION_PROMPT.format(
            instruction=experiment["question"],
            response=experiment["generated_answer"],
            reference_answer=experiment["true_answer"],
        )
        messages = [
            {"role": "system", "content": "You are a fair evaluator language model."},
            {"role": "user", "content": eval_prompt},
        ]

        eval_result = evaluation_client.text_generation(
            eval_prompt, max_new_tokens=1000
        )
        try:
            feedback, score = [item.strip() for item in eval_result.split("[RESULT]")]
            experiment["eval_score_LLM_judge"] = score
            experiment["eval_feedback_LLM_judge"] = feedback
        except:
            print(f"Parsing failed - output was: {eval_result}")

    results[system_type] = pd.DataFrame.from_dict(outputs)
    results[system_type] = results[system_type].loc[~results[system_type]["generated_answer"].str.contains("Error")]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

Device set to use cpu
  0%|          | 0/65 [00:00<?, ?it/s]


AttributeError: 'TextGenerationPipeline' object has no attribute 'text_generation'

In [150]:
from huggingface_hub import InferenceClient
import pandas as pd
from tqdm import tqdm

evaluation_client = InferenceClient("meta-llama/Llama-3.1-70B-Instruct")

results = {}
for system_type, outputs in [
    ("agentic", outputs_agentic_rag),
    ("standard", outputs_standard_rag),
]:
    for experiment in tqdm(outputs):
        eval_prompt = EVALUATION_PROMPT.format(
            instruction=experiment["question"],
            response=experiment["generated_answer"],
            reference_answer=experiment["true_answer"],
        )

        # Conversational style prompt
        messages = [
            {"role": "system", "content": "You are a fair evaluator language model."},
            {"role": "user", "content": eval_prompt}
        ]

        response = evaluation_client.chat_completion(messages=messages, max_tokens=1000)

        eval_result = response.choices[0].message["content"]

        try:
            feedback, score = [item.strip() for item in eval_result.split("[RESULT]")]
            experiment["eval_score_LLM_judge"] = score
            experiment["eval_feedback_LLM_judge"] = feedback
        except Exception as e:
            print(f"Parsing failed - output was: {eval_result}")

    results[system_type] = pd.DataFrame.from_dict(outputs)
    results[system_type] = results[system_type].loc[
        ~results[system_type]["generated_answer"].str.contains("Error")
    ]


100%|██████████| 65/65 [01:16<00:00,  1.18s/it]


In [165]:
results['agentic']['generated_answer'][3]

'The purpose of the /healthcheck endpoint in the Datasets server API is not specified in the provided documents.'

In [166]:
results['standard']['generated_answer'][3]

"The /healthcheck endpoint in the Datasets server API is used to verify the operational status of the server or a specific service within it. It helps in monitoring the availability and readiness of the API to handle requests, ensuring that the service is up and running as expected. This is particularly useful in a production environment where continuous monitoring and automatic failover mechanisms may depend on the endpoint's response. However, the specific implementation details and response format for the /healthcheck endpoint are not provided in the given documents. To get more detailed information, you would typically refer to the API documentation or contact the service provider."

In [167]:
results['standard']['true_answer'][3]

'Ensure the app is running'

In [152]:
df_agentic = pd.DataFrame(results['agentic'])
df_agentic.head()

question  \
0  What architecture is the `tokenizers-linux-x64...   
1  What is the purpose of the BLIP-Diffusion mode...   
2  How can a user claim authorship of a paper on ...   
3  What is the purpose of the /healthcheck endpoi...   
4  What is the default context window size for Lo...   

                                         true_answer  \
0                          x86_64-unknown-linux-musl   
1  The BLIP-Diffusion model is designed for contr...   
2  By clicking their name on the corresponding Pa...   
3                          Ensure the app is running   
4                                         127 tokens   

                                          source_doc  \
0  huggingface/tokenizers/blob/main/bindings/node...   
1  huggingface/diffusers/blob/main/docs/source/en...   
2  huggingface/hub-docs/blob/main/docs/hub/paper-...   
3  huggingface/datasets-server/blob/main/services...   
4  huggingface/transformers/blob/main/docs/source...   

                                    generated_answer eval_score_LLM_judge  \
0  The `tokenizers-linux-x64-musl` binary is desi...                    2   
1  The purpose of the BLIP-Diffusion model is not...                    2   
2  Unfortunately, no answer could be obtained fro...                    1   
3  The purpose of the /healthcheck endpoint in th...                    1   
4  The default context window size for Local Atte...                    1   

                             eval_feedback_LLM_judge  
0  Feedback: The response is somewhat complete an...  
1  Feedback: The response is somewhat complete, a...  
2  Feedback: The response is completely incomplet...  
3  Feedback: The response is incomplete and not f...  
4  Feedback: The response is incomplete and not f...

In [159]:
df_agentic['eval_score_LLM_judge'].astype(int).value_counts()

eval_score_LLM_judge
1    35
2    24
3     6
Name: count, dtype: int64

In [155]:
df_std = pd.DataFrame(results['standard'])
df_std.head()

question  \
0  What architecture is the `tokenizers-linux-x64...   
1  What is the purpose of the BLIP-Diffusion mode...   
2  How can a user claim authorship of a paper on ...   
3  What is the purpose of the /healthcheck endpoi...   
4  What is the default context window size for Lo...   

                                         true_answer  \
0                          x86_64-unknown-linux-musl   
1  The BLIP-Diffusion model is designed for contr...   
2  By clicking their name on the corresponding Pa...   
3                          Ensure the app is running   
4                                         127 tokens   

                                          source_doc  \
0  huggingface/tokenizers/blob/main/bindings/node...   
1  huggingface/diffusers/blob/main/docs/source/en...   
2  huggingface/hub-docs/blob/main/docs/hub/paper-...   
3  huggingface/datasets-server/blob/main/services...   
4  huggingface/transformers/blob/main/docs/source...   

                                    generated_answer eval_score_LLM_judge  \
0  The `tokenizers-linux-x64-musl` binary is desi...                    2   
1  The provided documents do not contain specific...                    2   
2  To claim authorship of a paper on the Hugging ...                    1   
3  The /healthcheck endpoint in the Datasets serv...                    2   
4  The retrieved documents do not provide informa...                    1   

                             eval_feedback_LLM_judge  
0  Feedback: The response is somewhat complete, a...  
1  Feedback: The response is somewhat complete, a...  
2  Feedback: The response is not accurate and not...  
3  Feedback: The response is somewhat complete, a...  
4  Feedback: The response is incomplete and does ...

In [158]:
df_std['eval_score_LLM_judge'].astype(int).value_counts()

eval_score_LLM_judge
2    33
1    17
3    15
Name: count, dtype: int64

In [141]:
DEFAULT_SCORE = 2 # Give average score whenever scoring fails
def fill_score(x):
    try:
        return int(x)
    except:
        return DEFAULT_SCORE

for system_type, outputs in [
    ("agentic", outputs_agentic_rag),
    ("standard", outputs_standard_rag),
]:

    results[system_type]["eval_score_LLM_judge_int"] = (
        results[system_type]["eval_score_LLM_judge"].fillna(DEFAULT_SCORE).apply(fill_score)
    )
    results[system_type]["eval_score_LLM_judge_int"] = (results[system_type]["eval_score_LLM_judge_int"] - 1) / 2

    print(
        f"Average score for {system_type} RAG: {results[system_type]['eval_score_LLM_judge_int'].mean()*100:.1f}%"
    )

Average score for agentic RAG: 26.2%
Average score for standard RAG: 46.2%


**Let us recap: the Agent setup improves scores by 14% compared to a standard RAG!** (from 73.1% to 86.9%)

This is a great improvement, with a very simple setup 🚀

(For a baseline, using Llama-3-70B without the knowledge base got 36%)